In [1]:
# Configure Jupyter so figures appear in the notebook
%matplotlib inline

# Configure Jupyter to display the assigned value after an assignment
%config InteractiveShell.ast_node_interactivity='last_expr_or_assign'

# import functions from the modsim.py module

from modsim import *

import pandas as pd

from pandas import read_html

import numpy as np

In [2]:
def eval_gs():
    #Amount of evaportanted water per second (kg/s)

    # (25 + 19v): evaporation coefficient

    # v: velocity of air above water surface (m/s)
    v = 6.7056

    #evaporation coefficient (kg/m^2h)
    theta = (25 + 19 * v)

    #water surface area (m^2)
    A = 360000000000

    # xs: max humidity ratio of saturated air (kg water / kg dry air)
    xs =  0.62198

    # x: humidity ratio air (kg water / kg dry air)
    x = 0.01062

    return theta * A * (xs - x) / 3600

In [20]:
params = Params(
#     surface_temp = pd.read_csv('sea-surface-temp_g-1.csv', header = 1),
#                 heat_constant = pd.read_csv('temp.csv', header = 2),
                gs = eval_gs(), t_0=0, t_end=120)

gs       9.317518e+09
t_0      0.000000e+00
t_end    1.200000e+02
dtype: float64

In [21]:
# heat_constant = pd.read_csv('temp.csv', header = 0)
# heat_constant

In [5]:
def pick_constant(heat_constant):
    input = 15
    trim_temp = heat_constant["Temperature"][3:36]
    for data in trim_temp:
        data = int(data)
        data -= input
        data = abs(data)
        print(data)
        out = np.min(data)
    print(out)
    type (data)


In [6]:




def make_system(params):
    """Makes a System object with the given parameters.
    
    params: sequence of G0, k1, k2, k3
    data: DataFrame with `glucose` and `insulin`
    
    returns: System object
    """
    gamma, mu, tao, beta, rho, alpha, sigma, delta, pi, t_0, t_end = params
    

    init = State(R=200, L=0, E=0, V=4e-7)

    
    return System(params,
                  init=init,gamma=gamma, mu=mu, tao=tao, beta=beta, rho=rho, alpha=alpha, sigma=sigma, delta=delta, pi=pi,
                  t_0=t_0, t_end=t_end, dt=(80/(60*24)))

In [8]:
def update_func(state, t, system):
    # stock values are stored in system.state
    # 
    R, L, E, V = state
    gamma, mu, tao, beta, rho, alpha, sigma, delta, pi = system.gamma, system.mu, system.tao, system.beta, system.rho, system.alpha, system.sigma, system.delta, system.pi
            
    dt=system.dt
    
    dRdt = gamma*tao-mu*R-beta*R*V
    dLdt = rho*beta*R*V-mu*L-alpha*L
    dEdt = (1-rho)*beta*R*V +alpha*L - delta*E
    dVdt = pi*E -sigma*V
    
    R += dRdt*dt
    L += dLdt*dt
    E += dEdt*dt
    V += dVdt*dt
    return State(R=R, L=L, E=E, V=V)


In [9]:
def run_simulation(system, update_func):
    """Runs a simulation of the system.
        
    system: System object
    update_func: function that updates state
    
    returns: TimeFrame
    """
    init = system.init
    t_0, t_end, dt = system.t_0, system.t_end, system.dt
    
    frame = TimeFrame(columns=init.index)
    frame.row[t_0] = init
    ts = linrange(t_0, t_end, dt)
    
    for t in ts:
        frame.row[t+dt] = update_func(frame.row[t], t, system)
    
    return frame


In [11]:
init = State(T=24)

T    24
dtype: int64

In [12]:
# water energy
q = System(init=init,
           m=1,
           cp=4190,
           t_0=0,
           t_end=100,
           T_env=24,
           dt=1)

# m: mass (kg)

# cp: specific heat of substance (J/kg deg C); water is 4190

# dt: change in temperature (deg C)

# q: thermal energy per kg of water
# q = m * cp * dt

init     T    24
dtype: int64
m                           1
cp                       4190
t_0                         0
t_end                     100
T_env                      24
dt                          1
dtype: object

In [13]:
def update_func(state, t, system):
    """Update the thermal transfer model.
    
    state: State (temp)
    t: time
    system: System object
    
    returns: State (temp)
    """
    r, dt = system.r, system.T_env, system.dt
    
    T = state.T
    T += -r * (T - T_env) * dt
    
    return State(T=T)

In [30]:
 # water evaporation rate
# gs: water evaporated per second (kg/s)
# # (25 + 19v): evaporation coecient
# # v: velocity of air above water surface
# v = 75
# # A: water surface area (m^2)
# A = 1
# # xs: max humidity ratio of saturated air (kg water / kg dry air)
# # xs =
# # x: humidity ratio air (kg water / kg dry air)
# # x =
# gs = (25 + 19 * v) * A * (xs - x) / 3600


In [31]:
def heat(ocean_temp, gs):
    
    #heat supplied (kJ/s (kW))
    hwe = 5
#     evaporation heat of water  (kJ/kg)
    kW = 3412 
#     Btu/h

    return 

In [37]:
# atmospheric energy

# R: gas constant for dry air in atmosphere
R = 8.31432 * 10 ** 3

# T: temperature of air
T = 5

# u: total energy per kg of air
u = (5 / 2) * R * T

103929.0